In [5]:
import os
import glob
from pathlib import Path
import json
import subprocess
import time
from tqdm import tqdm

import sys
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

import matplotlib.pyplot as plt
import torch
import torchvision
import torch.nn as nn
import torch.backends.cudnn as cudnn
from torch.autograd import Variable
import numpy as np
import cv2
if torch.cuda.is_available():
    torch.set_default_tensor_type('torch.cuda.FloatTensor')

from ssd import build_ssd

In [2]:
DATASET_PATH = '/home/stud_lab_vk_01/ad-detection/data/processed/LogoDet1YoloV4_filter'
train_imgs = glob.glob(os.path.join(DATASET_PATH, 'images', 'train', '**.jpg'))
val_imgs = glob.glob(os.path.join(DATASET_PATH, 'images', 'val', '**.jpg'))

In [3]:
WEIGHT_PATH = '/home/stud_lab_vk_01/ssd.pytorch/default_weights/ssd300_COCO_395000.pth'
net = build_ssd('test', 300, 2)
net.load_weights(WEIGHT_PATH)

Loading weights into state dict...
Finished!


/home/stud_lab_vk_01/ssd.pytorch/ssd.py:34: UserWarning: volatile was removed and now has no effect. Use `with torch.no_grad():` instead.
  self.priors = Variable(self.priorbox.forward(), volatile=True)


In [7]:
len(train_imgs)

156552

In [ ]:
import warnings
warnings.filterwarnings('ignore')

In [11]:
# clean train
PART = 'train'
THRESHOLD = 0.75

n_deleted = 0
for img_p in tqdm(train_imgs):
    img_name = Path(img_p).stem
    label_path = os.path.join(DATASET_PATH, 'labels', PART, f'{img_name}.txt')
    try:
        with open(label_path, 'r') as fd:
            boxes = fd.readlines()
        n_boxes = len(boxes)

        # read img and get number of predicted boxes
        img = cv2.imread(img_p)
        img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        x = cv2.resize(img, (300, 300)).astype(np.float32)
        x -= (104.0, 117.0, 123.0)
        x = x.astype(np.float32)
        x = x[:, :, ::-1].copy()
        x = torch.from_numpy(x).permute(2, 0, 1)
        xx = x.unsqueeze(0)
        if torch.cuda.is_available():
            xx = xx.cuda()
        y = net(xx)
        detections = y.data
        scale = torch.Tensor(img.shape[1::-1]).repeat(2)
        scores = []
        boxes = []
        for i in range(detections.size(1)):
            for j in range(detections.size(2)):
                score = detections[0,i,j,0]
                if score > 0.2:
                    pt = (detections[0,i,j,1:]*scale).cpu().squeeze().unsqueeze(0)
                    boxes.append(pt)
                    scores.append(score)
        scores = torch.tensor(scores)
        boxes = torch.cat(boxes, dim=0)
        boxes_ixs = torchvision.ops.nms(boxes.cpu(), scores.cpu(), iou_threshold=0.2)
        
        boxes = boxes[boxes_ixs]
        scores = scores[boxes_ixs]
        good_scores = scores[scores > THRESHOLD]
        if len(good_scores) - n_boxes > 1:
            n_deleted += 1
            os.remove(img_p)
            os.remove(label_path)
    except Exception as e:
        print('Remove', img_name)
        if os.path.exists(img_p):
            os.remove(img_p)
        if os.path.exists(label_path):
            os.remove(label_path)

  0%|          | 0/156552 [00:00<?, ?it/s]

/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:216: UserWarning: An output with one or more elements was resized since it had shape [199], which does not match the required output shape [174]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/ATen/native/Resize.cpp:30.)
  torch.index_select(x1, 0, idx, out=xx1)
/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:217: UserWarning: An output with one or more elements was resized since it had shape [199], which does not match the required output shape [174]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/

Remove rickard's dark___50


/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:216: UserWarning: An output with one or more elements was resized since it had shape [175], which does not match the required output shape [137]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/ATen/native/Resize.cpp:30.)
  torch.index_select(x1, 0, idx, out=xx1)
/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:217: UserWarning: An output with one or more elements was resized since it had shape [175], which does not match the required output shape [137]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/

Remove frame_000026


...

Remove frame_000082


/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:216: UserWarning: An output with one or more elements was resized since it had shape [168], which does not match the required output shape [135]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/ATen/native/Resize.cpp:30.)
  torch.index_select(x1, 0, idx, out=xx1)
/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:217: UserWarning: An output with one or more elements was resized since it had shape [168], which does not match the required output shape [135]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/

Remove frame_000013


/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:216: UserWarning: An output with one or more elements was resized since it had shape [168], which does not match the required output shape [153]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/ATen/native/Resize.cpp:30.)
  torch.index_select(x1, 0, idx, out=xx1)
/home/stud_lab_vk_01/ssd.pytorch/layers/box_utils.py:217: UserWarning: An output with one or more elements was resized since it had shape [168], which does not match the required output shape [153]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at /pytorch/aten/src/

KeyboardInterrupt: 